# Lab 4.2: Creación de *métricas* personalizadas en watsonx.governance

Los métricas son medidas **cuantitativas** del rendimiento del modelo que pueden ser evaluadas, monitorizadas, y que generalmente queremos optimizar. Por ejemplo, la precisión, la recuperación y la puntuación F1 son métricas. En este lab, utilizaremos el SDK de Python para el servicio de [IBM Watson OpenScale](https://dataplatform.cloud.ibm.com/docs/content/wsj/model/getting-started.html?context=cpdaas&audience=wdp) de watsonx.governance para crear *metricas* para un prompt de IA generativa personalizadas a los necesidades/requisitos de nuestro caso de uso.

In [ ]:
! pip install --upgrade openai azure-identity --no-cache
! pip install --upgrade ibm-watson-openscale --no-cache

In [ ]:
# importa las librerías necesarias
import os
import asyncio
import re
import json
from datetime import datetime, timezone
# librerias de IBM watsonxxxw
from ibm_watson_openscale.client import WatsonOpenScaleV2Adapter as OpenScaleClient, CloudPakForDataAuthenticator
from ibm_watsonx_ai import APIClient as WatsonxAIClient, Credentials
from ibm_watsonx_ai.foundation_models.prompts import PromptTemplateManager
# librerias de openai
from azure.identity import ClientSecretCredential, get_bearer_token_provider
from openai import AsyncAzureOpenAI
# otras
import pandas as pd

from IPython.display import display, Markdown

Configuración de las credenciales:

In [2]:
API_KEY = "<YOUR API KEY HERE>"
URL = "<YOUR URL HERE>"
USERNAME = "<YOUR USERNAME HERE>"
PASSWORD = "<YOUR PASSWORD HERE>"
# si ejecutas desde un entorno de IBM Cloud Pak for Data, puedes obtener el PROJECT_ID de la variable de entorno PROJECT_ID
PROJECT_ID = os.getenv('PROJECT_ID', "<YOUR PROJECT ID HERE>")

# credenciales de Azure (mismas que el laboratorio anterior)
AZURE_OPENAI_ENDPOINT = "<EDIT>"
AZURE_OPENAI_DEPLOYMENT_NAME = "<EDIT>"
AZURE_CLIENT_ID = "<EDIT>"
AZURE_CLIENT_SECRET = "<EDIT>"
AZURE_TENANT_ID = "<EDIT>"

Inicializamos los clientes de watsonx.ai y OpenScale.

In [3]:
creds = Credentials(
    api_key=API_KEY,
    url=URL,
    username=USERNAME,
    password=PASSWORD,
    instance_id="openshift"
)
# Inicialización de clientes
# cliente de watsonx.ai
watsonx_ai_client = WatsonxAIClient(credentials=creds, project_id=PROJECT_ID)
# cliente de Watson OpenScale (Monitorización y evaluación de modelos)
wos_client = OpenScaleClient(
    authenticator=CloudPakForDataAuthenticator(
        url=URL,
        apikey=API_KEY,
        username=USERNAME,
    ),
    service_url=URL,
)

Lista los prompt templates disponibles en el proyecto:

In [ ]:
prompt_mgr = PromptTemplateManager(api_client=watsonx_ai_client, project_id=PROJECT_ID)

# List prompt templates
templates_df = prompt_mgr.list(limit=5)  # Lists 5 most recent templates
templates_df

Selecciona el prompt template que queremos evaluar (en este caso, el que creamos en el lab 3):

In [ ]:
# selecciona el prompt template a utilizar
prompt_template_id = templates_df.iloc[0]['ID'] #"<ID DEL PROMPT TEMPLATE A UTILIZAR>"
print(f"{prompt_template_id=}")
# obten detalles del prompt template
prompt_template = prompt_mgr.load_prompt(prompt_template_id)
prompt_template

Como en el lab anterior, fijamos un prefijo para asegurarnos que los nombres de los artefactos que vamos a crear sean únicos:

In [6]:
# evita usar espacio en blanco en el prefijo, así como letras mayúsculas y caracteres especiales
USER_PREFIX = "<tu_prefijo_de_usuario_aqui>" # ejemplo: "juanperez", "ssv", "jdoe"

Ahora vamos a crear un *prompt* para evaluar el prompt template seleccionado utilizando el mismo modelo de Azure OpenAI que utilizamos en el lab 3:

In [7]:
JUDGE_PROMPT = """
You have been called to rate the following response (suggestions) to a support ticket. 
Please rate the response on a scale of 1 to 10, where 1 is the worst and 10 is the best, providing a brief explanation for your rating.

Your answer should be provided in the following JSON format:

```json
{{
    "explanation": "Your explanation here",
    "rating": <your rating here> // an integer between 1 and 10
}}
```

Only provide the JSON object, do not include any other text.

Support ticket: {ticket}
Suggestions: 

{suggestions}
""".strip()
# patron de regex para extraer JSON de un texto
JSON_PATTERN = re.compile(r'(\{(?:[^{}]|\{(?:[^{}]*|\{[^{}]*\})*\})*\}|\[(?:[^\[\]]|\[(?:[^\[\]]*|\[[^\[\]]*\])*\])*\])', re.DOTALL)

Función para llamar al modelo de Azure OpenAI:

In [8]:
def get_azure_token_provider():
    default_scope = "https://cognitiveservices.azure.com/.default"
    credential = ClientSecretCredential(
        tenant_id = os.environ.get('AZURE_TENANT_ID', AZURE_TENANT_ID),
        client_id = os.environ.get('AZURE_CLIENT_ID' ,AZURE_CLIENT_ID),
        client_secret = os.environ.get('AZURE_CLIENT_SECRET', AZURE_CLIENT_SECRET)
    )
    token_provider = get_bearer_token_provider(credential, default_scope)
    return token_provider

async def generate_response(ticket:str, suggestions:str, max_tokens:int=200, token_provider=None) -> str:
    """Funcion para generar una respuesta con el prompt de evaluación para un ticket y sugerencias dado"""
    client = AsyncAzureOpenAI(
        azure_endpoint = os.environ.get('AZURE_OPENAI_ENDPOINT', AZURE_OPENAI_ENDPOINT),
        api_version = "2024-02-15-preview",
        azure_ad_token_provider = token_provider
    )
    model_response = await client.chat.completions.create(
        model = os.environ.get('AZURE_OPENAI_DEPLOYMENT_NAME', AZURE_OPENAI_DEPLOYMENT_NAME),
        messages = [{"role": "user", "content": JUDGE_PROMPT.format(ticket = ticket, suggestions = suggestions)}],
        max_tokens = max_tokens,
        # response_format={"type": "json_object"}
    )
    return model_response.choices[0].message.content

async def generate_responses_batch(tickets:list, answers:list, token_provider:object|None=None) -> list:
    token_provider = token_provider or get_azure_token_provider()
    summaries = await asyncio.gather(
        *[generate_response(ticket, answer, token_provider=token_provider) for ticket, answer in zip(tickets, answers)]
    )
    return summaries

def parse_rating_response(response:str) -> dict:
    """Funcion para extraer el JSON de una respuesta de evaluación"""
    match = JSON_PATTERN.search(response)
    if match:
        return json.loads(match.group())
    return {}

Cargamos los datos que vamos a utilizar para generar las metricas:

In [ ]:
ticket_suggestions_df = pd.read_csv("https://raw.githubusercontent.com/maialenespi/TEL-content/main/evaluation-tickets.csv").head(10)
ticket_suggestions_df

In [ ]:
ticket = ticket_suggestions_df.iloc[0]['ticket']
suggestions = ticket_suggestions_df.iloc[0]['generated_text']
# construimos el prompt y llamamos al modelo para obtener una evaluación de las sugerencias
prompt = JUDGE_PROMPT.format(ticket=ticket, suggestions=suggestions)
az_token_provider = get_azure_token_provider()
response = await generate_response(ticket, suggestions, token_provider=az_token_provider)
# # mostramos el resultado
json_resp = parse_rating_response(response)
rating = json_resp["rating"]
explanation = json_resp["explanation"]
suggestions_md = suggestions.replace('\n', '\n> ')
display(Markdown(f"""
### User Ticket:
                 
> {ticket}

### Sugerencias del modelo:

> {suggestions_md}

### Respuesta del LLM-as-a-Judge:

- Rating: `{rating}`/`10`
- Explanation:

    > {explanation}
""".strip()))

Ahora lo hacemos para todos los datos:

In [ ]:
all_responses = await generate_responses_batch(
    ticket_suggestions_df['ticket'].tolist(),
    ticket_suggestions_df['generated_text'].tolist(),
    token_provider=az_token_provider
)
all_responses_json = [parse_rating_response(resp) for resp in all_responses]
ticket_suggestions_df['rating'] = [resp.get("rating") for resp in all_responses_json]
ticket_suggestions_df['explanation'] = [resp.get("explanation") for resp in all_responses_json]
ticket_suggestions_df

In [ ]:
# Descripción de las evaluaciones
ticket_suggestions_df.rating.describe()

## Configura el monitor personalizado

In [16]:
from ibm_watson_openscale.integrated_systems import IntegratedSystems
from ibm_watson_openscale.base_classes.watson_open_scale_v2 import (
    MonitorMetricRequest,
    MonitorMeasurementRequest,
    MetricThreshold,
    MonitorTagRequest,
    Target,
    ApplicabilitySelection
)
from ibm_watson_openscale.supporting_classes.enums import (
    MetricThresholdTypes,
    TargetTypes
)

In [ ]:
# configurar valores para el proveedor de métricas personalizadas y la definición del monitor
CUSTOM_MONITOR_NAME = USER_PREFIX+'-LLM-as-a-judge Monitor'
CUSTOM_METRICS_PROVIDER_NAME = USER_PREFIX+'-LLM-as-a-judge Support Ticket Scoring'
TAGS= ['region']
TAG_DESCRIPTION =['LLMAAJ'] 

# Habilitar la programación para tu monitor personalizado. Actualiza el valor a True/False si deseas habilitar/deshabilitar la programación.
# Esto está desactivado por defecto, porque ejecutar el monitor puede ser bastante costoso
ENABLE_SCHEDULE = False
MONITOR_DESCRIPTION = USER_PREFIX+'-LLMAAJ Ticket Classifier Monitor'
print(f"Se creará un monitor personalizado con el nombre '{CUSTOM_MONITOR_NAME}'")

Definitmos el tipo de entrada y algoritmos que aplican al monitor

In [21]:
# tipo de datos de entrada de tu modelo.
# Los tipos de datos de entrada compatibles son "structured", "unstructured_text", "unstructured_image"
input_data_type = ["unstructured_text"]
# los tipos de algoritmos que tu modelo soporta.
# Los tipos de algoritmos de modelo compatibles son "binary", "multiclass", "regression", "generation"
algorithm_types = ["regression"] # decimos que es regresion porque el modelo devuelve un valor numerico entre 1 y 10
problem_type_selection = ApplicabilitySelection(problem_type=algorithm_types)
input_data_type_selection = ApplicabilitySelection(input_data_type=input_data_type)

Creamos la definición de metrica personalizada especificando tambien los umbrales de alerta por defecto para esa métrica 

In [28]:
metrics = [
    MonitorMetricRequest(
        name=USER_PREFIX+'_llmaaj_score', 
        applies_to=problem_type_selection,
        expected_direction='increasing',
        description=USER_PREFIX+'-LLM-as-a-judge Description',                                                              
        thresholds=[MetricThreshold(type=MetricThresholdTypes.LOWER_LIMIT, default=5),
                    MetricThreshold(type=MetricThresholdTypes.UPPER_LIMIT, default=10)],
    )
    ]
# definimos las tags que aplican al monitor (opcional)
tags = [MonitorTagRequest(name=TAGS[0], description=TAG_DESCRIPTION[0])]

Y ahora creamos el custom monitor en Watson OpenScale

In [ ]:
custom_monitor_details = wos_client.monitor_definitions.add(
    name=CUSTOM_MONITOR_NAME, description=MONITOR_DESCRIPTION, metrics=metrics, tags=tags,
    applies_to=input_data_type_selection, background_mode=False#, monitor_runtime = monitor_runtime,
).result

**Nota:** Para eliminar un custom monitor existente se puede usar la función siguiente:

```python
custom_monitor_id = custom_monitor_details.metadata.id
wos_client.monitor_definitions.delete(monitor_definition_id=custom_monitor_id)
```

### Crea una instancia del monitor personalizado

Ahora que la definición de la métrica y monitor personalizado ha sido creado, podemos instanciar el monitor personalizado para el prompt que estamos evaluando.

In [31]:
data_mart_id = "00000000-0000-0000-0000-000000000000"
custom_monitor_id = custom_monitor_details.metadata.id
# obtener el id de la suscripción a ser monitorizada
subscriptions_result = wos_client.subscriptions.list(project_id=PROJECT_ID).result.to_dict()
assert len(subscriptions_result['subscriptions']) < 2, "More than one subscription found"
subscription_id = subscriptions_result['subscriptions'][0]['metadata']['id']

In [ ]:
target = Target(
    target_type=TargetTypes.SUBSCRIPTION,
    target_id=subscription_id
)
custom_monitor_instance_details = wos_client.monitor_instances.create(
            data_mart_id=data_mart_id,
            background_mode=False,
            monitor_definition_id=custom_monitor_id,
            target=target,
            parameters={}
).result
print(custom_monitor_instance_details)

### Evaluación y Publicación de las métricas a OpenScale (Push-Model) 

Si ya hemos evaluado nuestro modelo desde fuera de la plataforma, podemos enviar los resultados de la evaluación directamente a OpenScale para que las mantenga registradas. Esto se conoce como el modelo de *push* de métricas.

Otra opción es que OpenScale se conecte automáticamente a una función de evaluación que hemos desplegado como un servicio REST (modelo *pull*). En este caso, tendríamos que desplegar la función de Python de evaluación a su propio endpoint y configurar la integración con OpenScale para que se conecte a ella cada vez que se realice una evaluación.

En este lab, utilizaremos el modelo de *push* de métricas, ya que el despliegue de una función de evaluación como un servicio REST es un proceso más complejo y que conlleva un mayor tiempo de desarrollo y mayor uso de recursos. Sin embargo, si estás interesado en aprender cómo hacerlo, puedes consultar [este notebook de Python en GitHub]() que demuestra el proceso (recomendado para usuarios avanzados).

Listamos los datos que ha logeado OpenScale para que podamos ver como se han registrado:

In [ ]:
# listamos los datasets de payload logging asociados a la suscripción y seleccionamos el primero
# para obtener su id
payload_dataset_id = wos_client.data_sets.list(
    project_id=PROJECT_ID,
    target_target_id=subscription_id,
    target_target_type="subscription",
    type="payload_logging"
).result.data_sets[0].metadata.id
# mostramos los primeros 5 registros del dataset de payload logging
wos_client.data_sets.show_records(
    data_set_id = payload_dataset_id,
    limit=5
)

Publicamos las métricas a nuestro monitor personalizado

In [ ]:
# obtenemos los scores antes obtenidos del LLM como juez
llmaaj_scores = ticket_suggestions_df.rating.tolist()
# calculamos el promedio de los scores de las evaluaciones
avg_llmaaj_score = round(sum(llmaaj_scores) / len(llmaaj_scores), 4)
# listamos las variables que necesitaremos para publicar las métricas
timestamp = datetime.now(tz=timezone.utc).strftime("%Y-%m-%dT%H:%M:%S.%fZ")
custom_monitor_id = custom_monitor_instance_details.entity.monitor_definition_id
custom_monitor_instance_id = custom_monitor_instance_details.metadata.id
# publicamos el score promedio al monitor como una métrica
monitor_measurement_requests = [
    MonitorMeasurementRequest(
        timestamp=timestamp,
        metrics=[{USER_PREFIX+'_llmaaj_score': avg_llmaaj_score}],
        # run_id=custom_monitoring_run_id
    )
]
published_measurement_response = wos_client.monitor_instances.add_measurements(
    monitor_instance_id=custom_monitor_instance_id,
    monitor_measurement_request=monitor_measurement_requests
).result
published_measurement_id = published_measurement_response[0]["measurement_id"]
print("Published Measurement ID", published_measurement_id)

 Ahora podemos hacer una petición para listar las metricas guardadas en OpenScale y verificar que la nueva metrica ha sido guardada correctamente.

In [ ]:
measurements = wos_client.monitor_instances.measurements.list(
    monitor_instance_id=custom_monitor_instance_id,
    start=timestamp,
    end=datetime.now(tz=timezone.utc).strftime("%Y-%m-%dT%H:%M:%S.%fZ")
).result.to_dict()
measurements